# Анализ и Визуализация Модели Сегментации Сцепки

Этот ноутбук предназначен для загрузки уже обученной модели (`.cbm` файл) и проведения всестороннего анализа ее качества на тестовых данных.

**Шаги:**
1.  **Настройка параметров:** Укажите пути к модели и данным.
2.  **Загрузка данных и модели:** Все необходимое загружается в память.
3.  **Количественный анализ:** Расчет и отображение `classification_report` и матрицы ошибок.
4.  **Визуальный анализ:** Построение 2D-проекций для визуализации ошибок на конкретной сцене.

In [ ]:
import pandas as pd
import numpy as np
import json
import os

from catboost import CatBoostClassifier
from sklearn.metrics import classification_report, confusion_matrix

import plotly.graph_objects as go
from plotly.subplots import make_subplots

def visualize_point_cloud(points: np.ndarray, colors: list) -> go.Figure:
    fig = go.Figure(data=[go.Scatter3d(
        x=points[:, 0], y=points[:, 1], z=points[:, 2],
        mode='markers',
        marker=dict(size=2, color=colors, opacity=0.8)
    )])
    fig.update_layout(
        title="Визуализация облака точек",
        scene=dict(
            xaxis_title='X (ось движения)',
            yaxis_title='Y (поперечная ось)',
            zaxis_title='Z (вертикальная ось)',
            aspectmode='data'
        ),
        margin=dict(r=0, b=0, l=0, t=40)
    )
    return fig

### Шаг 1: Настройка параметров

**ВАЖНО:** Заполните пути ниже. Укажите путь к файлу с моделью, которую хотите проанализировать, и к файлу с обработанными тестовыми данными (`.csv`).

In [ ]:
MODEL_PATH = "C://Users//PC//Documents//university//AI//PointCloudProject//models//best_hitch_detection_model_G3.cbm"

PROCESSED_TEST_DATA_PATH = "processed_test_data.csv"
PROCESSED_TRAIN_DATA_PATH = "processed_train_data.csv"

SCENE_ID_TO_ANALYZE = 0

### Шаг 2: Загрузка данных и модели

Эта ячейка загружает все необходимое в память. Просто запустите ее.

In [20]:
print(f"Загрузка модели из файла: {MODEL_PATH}")
model = CatBoostClassifier()
model.load_model(MODEL_PATH)
print("Модель успешно загружена.")

print(f"\nЗагрузка тестовых данных из файла: {PROCESSED_TEST_DATA_PATH}")

print("Тестовые данные успешно загружены. Размер:", test_dataframe.shape)

Загрузка модели из файла: C://Users//PC//Documents//university//AI//PointCloudProject//models//best_hitch_detection_model_G3.cbm
Модель успешно загружена.

Загрузка тестовых данных из файла: processed_test_data.csv
Тестовые данные успешно загружены. Размер: (1827360, 13)


In [ ]:
test_dataframe = pd.read_csv(PROCESSED_TEST_DATA_PATH)
train_dataframe = pd.read_csv("processed_train_data.csv")
display(train_dataframe.head())

print("\nАбсолютное количество точек по классам:")
value_counts = train_dataframe['label'].value_counts()
print(value_counts)

print("\nСоотношение классов в процентах:")
normalized_counts = train_dataframe['label'].value_counts(normalize=True) * 100
print(normalized_counts.map('{:.2f}%'.format))

x         y         z  eigenvals_sum     linearity  planarity  \
0  4.842968 -0.734604  4.309388   3.319105e-03  2.261989e-01   0.709226   
1  5.246977 -0.882197  4.282535   5.419204e-03  2.638065e-01   0.650388   
2 -1.095965 -0.037342  4.826015   8.980336e-31  8.980336e-23   0.000000   
3  6.718125 -1.327618  4.182507   1.476375e-02  9.785893e-01   0.019533   
4 -1.095965 -0.037342  4.826015   8.980336e-31  8.980336e-23   0.000000   

   change_of_curvature  scattering  omnivariance    anisotropy  eigenentropy  \
0             0.035123    0.064570      0.000665  9.354249e-01  8.130589e-01   
1             0.047093    0.085802      0.001185  9.141944e-01  8.393265e-01   
2             0.000000    0.000000      0.000000  8.980336e-23  1.654239e-21   
3             0.001834    0.001877      0.000494  9.981223e-01  1.149613e-01   
4             0.000000    0.000000      0.000000  8.980336e-23  1.654239e-21   

   label  scene_id  
0      0         0  
1      0         0  
2      0         0  
3      0         0  
4      0         0


Абсолютное количество точек по классам:
label
0    12184816
1      148592
Name: count, dtype: int64

Соотношение классов в процентах:
label
0    98.80%
1     1.20%
Name: proportion, dtype: object


### Шаг 3: Количественный анализ (Отчет и Матрица ошибок)

Здесь мы оцениваем качество модели на *всей* тестовой выборке.

In [ ]:
X_test = test_dataframe.drop(columns=["label","scene_id"])
y_test_true = test_dataframe['label']

y_test_pred = model.predict(X_test)

print("\n--- Отчет по классификации (Classification Report) ---")
print(classification_report(y_test_true, y_test_pred, target_names=['Фон (0)', 'Сцепка (1)']))

print("\n--- Матрица ошибок (Confusion Matrix) ---")
cm = confusion_matrix(y_test_true, y_test_pred)
print("Матрица:\n", cm)


axis_labels = ['Фон (0)', 'Сцепка (1)']
fig_cm = go.Figure(data=go.Heatmap(
                   z=cm,
                   x=['Предсказан ' + label for label in axis_labels],
                   y=['Истинный ' + label for label in axis_labels],
                   hoverongaps=False, text=cm, texttemplate="%{text}", colorscale='Blues'))

fig_cm.update_layout(
    title=f'Матрица ошибок для модели: {os.path.basename(MODEL_PATH)}',
    xaxis_title='Предсказанный класс', yaxis_title='Истинный класс')
fig_cm.show()


--- Отчет по классификации (Classification Report) ---
              precision    recall  f1-score   support

     Фон (0)       1.00      1.00      1.00   1794056
  Сцепка (1)       0.99      0.88      0.93     33304

    accuracy                           1.00   1827360
   macro avg       1.00      0.94      0.97   1827360
weighted avg       1.00      1.00      1.00   1827360


--- Матрица ошибок (Confusion Matrix) ---
Матрица:
 [[1793886     170]
 [   4085   29219]]


### Шаг 4: Визуальный анализ ошибок (2D проекции)

Теперь посмотрим наглядно, где именно модель ошибается на примере одной сцены.
**Зеленый** - правильно найденная сцепка (TP).
**Серый** - правильно определенный фон (TN).
**Красный** - фон, ошибочно принятый за сцепку (FP).
**Фиолетовый** - точка сцепки, которую модель пропустила (FN).

In [ ]:
scene = test_dataframe[test_dataframe["scene_id"] == SCENE_ID_TO_ANALYZE].copy()

if scene.empty:
    print(f"Ошибка: Сцена с ID {SCENE_ID_TO_ANALYZE} не найдена в тестовых данных!")
else:
    
    X_test_scene = scene.drop(columns=["label","scene_id"])
    y_true_scene = scene['label'].to_numpy()
    y_pred_scene = model.predict(X_test_scene).flatten()
  
    error_labels = np.zeros_like(y_true_scene)
    error_labels[(y_true_scene == 0) & (y_pred_scene == 0)] = 0 # TN
    error_labels[(y_true_scene == 1) & (y_pred_scene == 1)] = 1 # TP
    error_labels[(y_true_scene == 0) & (y_pred_scene == 1)] = 2 # FP
    error_labels[(y_true_scene == 1) & (y_pred_scene == 0)] = 3 # FN
  
    error_color_map = {
        0: 'lightgrey', 1: 'green',
        2: 'red',       3: 'magenta'
    }
    points_scene = scene[['x', 'y', 'z']].to_numpy()
    error_colors = [error_color_map.get(label, 'black') for label in error_labels]

    
    print("\n--- 3D Визуализация ошибок ---")
    fig_3d_errors = visualize_point_cloud(points_scene, error_colors)
    fig_3d_errors.update_layout(title=f'3D Визуализация ошибок для сцены {SCENE_ID_TO_ANALYZE}')
    fig_3d_errors.show()
    
    
    print("\n--- 2D Визуализация ошибок (проекции) ---")
    fig_2d_errors = make_subplots(rows=1, cols=2,
                                  subplot_titles=('Вид сбоку (Оси X-Z)', 'Вид сверху (Оси X-Y)'))
  
    fig_2d_errors.add_trace(go.Scatter(
        x=points_scene[:, 0], y=points_scene[:, 2], mode='markers',
        marker=dict(color=error_colors, size=3), name='Вид сбоку'), row=1, col=1)
  
    fig_2d_errors.add_trace(go.Scatter(
        x=points_scene[:, 0], y=points_scene[:, 1], mode='markers',
        marker=dict(color=error_colors, size=3), name='Вид сверху'), row=1, col=2)
  
    fig_2d_errors.update_xaxes(title_text="Ось X", row=1, col=1); fig_2d_errors.update_yaxes(title_text="Ось Z (высота)", row=1, col=1)
    fig_2d_errors.update_xaxes(title_text="Ось X", row=1, col=2); fig_2d_errors.update_yaxes(title_text="Ось Y (ширина)", row=1, col=2)
    fig_2d_errors.update_layout(
        title_text=f'2D Визуализация ошибок для сцены {SCENE_ID_TO_ANALYZE}', showlegend=False, height=500)
  
    fig_2d_errors.show()


--- 3D Визуализация ошибок ---



--- 2D Визуализация ошибок (проекции) ---


---
### Шаг 4: Визуальный анализ (Ground Truth и Предсказания)

Теперь посмотрим наглядно на примере одной сцены. Сначала отобразим **истинную разметку (Ground Truth)**, а затем — **предсказания модели** и **карту ошибок**.

**Цветовая схема для Ground Truth и Предсказаний:**
*   **Желтый** - Сцепка (класс 1)
*   **Зеленый** - Фон (класс 0)

In [ ]:
scene = test_dataframe[test_dataframe["scene_id"] == SCENE_ID_TO_ANALYZE].copy()

if scene.empty:
    print(f"Ошибка: Сцена с ID {SCENE_ID_TO_ANALYZE} не найдена в тестовых данных!")
else:
    points_gt = scene[['x', 'y', 'z']].to_numpy()
    labels_gt = scene['label'].astype(int)

    color_map_gt = {
        0: 'green',
        1: 'yellow'
    }
    colors_gt = [color_map_gt.get(label, 'black') for label in labels_gt]

    fig_gt = visualize_point_cloud(points_gt, colors_gt)
    fig_gt.update_layout(title=f'Истинная разметка (Ground Truth) для Сцены {SCENE_ID_TO_ANALYZE}')
    fig_gt.show()

In [ ]:
y_pred_scene = model.predict(scene.drop(columns=["label","scene_id"])).flatten()

colors_pred = [color_map_gt.get(label, 'black') for label in y_pred_scene]

fig_pred = visualize_point_cloud(points_gt, colors_pred)
fig_pred.update_layout(title=f'Предсказания модели для Сцены {SCENE_ID_TO_ANALYZE}')
fig_pred.show()